In [0]:
#@title Install gspread
!pip install --upgrade -q gspread

In [0]:
#@title Import Strava activitities from Google Sheets

from google.colab import auth
auth.authenticate_user()

import gspread
from oauth2client.client import GoogleCredentials

gc = gspread.authorize(GoogleCredentials.get_application_default())

worksheet = gc.open('Strava 2018-07-02').sheet1

# get_all_values gives a list of rows.
rows = worksheet.get_all_values()

# Convert to a DataFrame and render.
import pandas as pd
activities_raw = pd.DataFrame.from_records(rows[1:], columns=rows[0]);

In [0]:
#@title Index activities, convert data types, convert units
activities = activities_raw.copy()

# Project
activities = activities[['date', 'type', 'distance', 'elapsed_time', 'commute', 'name']]

# Set data types
activities['distance'] = activities['distance'].astype(float)
activities['elapsed_time'] = activities['elapsed_time'].astype(float)
activities['commute'] = activities['commute'].apply(lambda x: 1 if x == 'TRUE' else 0).astype(int)

# Convert units
activities['distance'] = activities['distance'] / 1000
activities['elapsed_time'] = activities['elapsed_time'] / 60

# Number of activities (at this aggregation level, trivially 1)
activities['count'] = 1

# Index
activities['date'] = pd.to_datetime(activities_raw['date'])
activities.set_index(['date', 'type'], inplace=True)

In [0]:
#@title Define formatters for readability
formatters = {
    'distance': '{:.0f}km'.format,
    'elapsed_time':' {:.0f}min'.format,
}

detailed_formatters = {
    'distance': '{:.1f}km'.format,
    'elapsed_time':' {:.1f}min'.format,
}

In [0]:
#@title Print a few random activities
print(
    activities[['distance', 'elapsed_time', 'commute', 'count']]
      .sample(5)
      .sort_index()
      .to_string(formatters=formatters))

In [0]:
#@title Print totals
print(
    activities
      .groupby(level='type')
      .sum()
      .sort_values(by='count', ascending=False)
      .to_string(formatters=formatters))

In [0]:
#@title Show date range

first_date = activities.index.levels[0].min()
last_date = activities.index.levels[0].max()
print('Activities recorded from %s to %s, total of %d days.' % (
    first_date.strftime('%Y-%m-%d'),
    last_date.strftime('%Y-%m-%d'),
    (last_date - first_date).days))

In [0]:
#@title Activities with the longest distance
print(
    activities['distance']
        .groupby('type').nlargest(3)
        .to_string(float_format='%.1fkm'))

In [0]:
#@title Activities with the longest duration
print(
    (activities['elapsed_time']
        .groupby('type').nlargest(4) / 60)
        .to_string(float_format='%.1fh'))

In [0]:
#@title Summarize by day and activity type
import numpy as np

activities_by_day_type = (
    activities
        .groupby([pd.Grouper(freq='D', level=0), 'type'])
        .sum())

activities_by_day_type = (
    activities_by_day_type
        .reset_index(level='type')
        .to_period('D')
        .reset_index()
        .set_index(['date', 'type']))

first_day = activities_by_day_type.index.levels[0].min()
last_day = activities_by_day_type.index.levels[0].max()
days = pd.period_range(first_day, last_day, freq='D')
types = activities_by_day_type.index.levels[1].unique()
index = pd.MultiIndex.from_product([days, types], names=['day', 'type'])
activities_by_day_type = activities_by_day_type.reindex(index, fill_value=0)

In [0]:
#@title Print a few days
print(activities_by_day_type.tail(12).to_string(formatters=formatters))

In [0]:
#@title Activities by day
activities_by_day = activities_by_day_type.groupby('day').sum()

In [0]:
#@title Activities by type
activities_by_type = activities_by_day_type.groupby('type').sum()

In [0]:
#@title Daily average
print(
    activities_by_day[['distance', 'elapsed_time']]
        .mean()
        .to_frame('mean')
        .T
        .to_string(formatters=detailed_formatters))

In [0]:
#@title Quick sanity check

print("average distance per day: %.1fkm" % (
    activities['distance'].sum() /
    (last_day - first_day)))
print("average time per day: %.1fmin" % (
    activities['elapsed_time'].sum() /
    (last_day - first_day)))

In [0]:
#@title Find days, months, quarters, years with extremes

frequencies = ['D', 'M', 'Q', 'Y']

for f in frequencies:
  extremes_by_type = (
    activities_by_day_type
      .unstack('type')
      .groupby(pd.Grouper(freq=f)).sum()
      .agg(['idxmax', 'max']))
  extremes_by_type.index = [f, 'max']

  print(
    extremes_by_type.T
      .unstack(level=0)
      .swaplevel(axis=1)
      .sort_index(axis=1))
  print('freq=%s\n' % f)

In [0]:
#@title Weekdays with largest means
weekday_abbr = 'Mon Tue Wed Thu Fri Sat Sun'.split()
print(
    activities_by_day_type[['distance', 'elapsed_time', 'commute', 'count']]
        .unstack('type')
        .groupby(lambda d: weekday_abbr[d.weekday]).mean()
        .agg(['idxmax', 'max'])
        .T.unstack(level=0)
        .swaplevel(axis=1).sort_index(axis=1))

In [0]:
#@title Months of the year with largest means
months = 'Jan Feb Mar Apr May Jun Jul Aug Sep Oct Nov Dec'.split()
print(
    activities_by_day_type[['distance', 'elapsed_time', 'commute', 'count']]
        .unstack('type')
        .groupby(pd.Grouper(freq='M')).sum()
        .groupby(lambda m: months[m.month-1]).mean()
        .agg(['idxmax', 'max'])
        .T.unstack(level=0)
        .swaplevel(axis=1).sort_index(axis=1))

In [0]:
#@title Quarters of the year with largest means
print(
    activities_by_day_type[['distance', 'elapsed_time', 'commute', 'count']]
        .unstack('type')
        .groupby(pd.Grouper(freq='Q')).sum()
        .groupby(lambda d: "Q%d" % d.quarter).mean()
        .agg(['idxmax', 'max'])
        .T.unstack(level=0)
        .swaplevel(axis=1).sort_index(axis=1))

In [0]:
#@title Plot running activity, quarterly, summed
import matplotlib.pyplot as plt
from matplotlib.ticker import StrMethodFormatter

fig, (ax1, ax2, ax3) = (
    plt.subplots(
        nrows=3, ncols=1,
        sharex=True, sharey=False,
        figsize=(8.025, 10)))

runs_q_sum = (
    activities.loc[(slice(None), 'Run'), :]
        .reset_index('type', drop=True)
        .to_period('D')
        .groupby(pd.Grouper(freq='Q')).sum())

runs_q_sum['distance'].plot(ax=ax1, kind='bar', color='#7799cc')
ax1.set_ylabel('km')
ax1.set_title('Distance')

(runs_q_sum['elapsed_time'] / 60).plot(ax=ax2, kind='bar', color='#7799cc')
ax2.set_ylabel('h')
ax2.set_title('Duration')

runs_q_sum['count'].plot(ax=ax3, kind='bar', color='#7799cc')
ax3.set_ylabel('number')
ax3.set_title('Count')

fig.autofmt_xdate()

In [0]:
#@title Plot running activity, quarterly, mean

from matplotlib import ticker

fig2, (ax4, ax5) = (
    plt.subplots(
        nrows=2, ncols=1,
        sharex=True, sharey=False,
        figsize=(8.025, 10/3*2)))

(runs_q_sum['distance'] / runs_q_sum['count']).plot(ax=ax4, kind='bar', color='#7799cc');
ax4.set_ylabel('km')
ax4.set_title('Mean distance')
ax4.yaxis.set_major_locator(ticker.MultipleLocator(5))

(runs_q_sum['elapsed_time'] / runs_q_sum['count']).plot(ax=ax5, kind='bar', color='#7799cc');
ax5.set_ylabel('min')
ax5.set_title('Mean duration')
ax5.yaxis.set_major_locator(ticker.MultipleLocator(60))

fig2.autofmt_xdate()

In [0]:
#@title Plot running activity, quarterly, median
fig3, (ax6, ax7) = (
    plt.subplots(
        nrows=2, ncols=1,
        sharex=True, sharey=False,
        figsize=(8.025, 10/3*2)))

runs_q_median = (
    activities.loc[(slice(None), 'Run'), :]
        .reset_index('type', drop=True)
        .to_period('D')
        .groupby(pd.Grouper(freq='Q')).median())

runs_q_median['distance'].plot(ax=ax6, kind='bar', color='#7799cc')
ax6.set_ylabel('km')
ax6.set_title('Median distance')

runs_q_median['elapsed_time'].plot(ax=ax7, kind='bar', color='#7799cc')
ax7.set_ylabel('min')
ax7.set_title('Median duration')
ax7.yaxis.set_major_locator(ticker.MultipleLocator(30))

fig3.autofmt_xdate()

In [0]:
#@title Plot running activity, quarterly, pace
fig4, (ax8, ax9) = (
    plt.subplots(
        nrows=2, ncols=1,
        sharex=True, sharey=False,
        figsize=(8.025, 10/3*2)))

(runs_q_sum['elapsed_time'] / runs_q_sum['distance']).plot(ax=ax8, kind='bar', color='#7799cc');
ax8.set_ylabel('min / km')
ax8.set_title('Pace')

(runs_q_sum['distance'] / (runs_q_sum['elapsed_time'] / 60)).plot(ax=ax9, kind='bar', color='#7799cc');
ax9.set_ylabel('km / h')
ax9.set_title('Speed')

fig4.autofmt_xdate()